# The Hodking-Huxley Model Neuron (updated to Julia 1.0)

We now numerically simulate and study the model proposed by Hodgkin and Huxley in the 1950s, describing the generation of the action potential in the giant axon of the squid. This model is characterised by four  state-variables (i.e. the membrane potential $V(t)$, the fraction of open potassium channels $n(t)$, and the fraction of open sodium channes - as described simultaneously by two additional state variables $m(t)$ and $h(t)$). All these variables evolve in time according to a system of *coupled* first-order ordinary differential equations, whose *external input* is the injected current (density) $I$ - here considered to be constant in time: 

\begin{eqnarray}
C \frac{dV(t)}{dt}\ =&\ G_{leak} (E_{leak} - V) + G_{Na} m^3 h (E_{Na} - V) + G_{K} n^4 (E_{K} - V) + I\\
 \frac{dn}{dt}\ =&\ \alpha_n (1 - n) - \beta_n n\\
 \frac{dm}{dt}\ =&\ \alpha_m (1 - m) - \beta_m m\\
 \frac{dh}{dt}\ =&\ \alpha_h (1 - h) - \beta_h h\\
\end{eqnarray}

In [ ]:
Pkg.add("Plots")
Pkg.add("Interact")

In [1]:
# Whatever follows the hash symbol is ignored and it is used to annotate or comment the code 
import Pkg;
import Pkg; 
using Plots;                           # Tells the computer to “add” a package for (later) generating plots
using Interact;                         # Tells the computer to “add” a package for (later) rendering a “sliders”
 
const T      = 300.;    # This represents the maximal lifetime of the simulation [ms]
 
const Δt     = 0.01;    # This is the minimal step by which t is incremented as time goes by [ms] - WATCH OUT! DO NOT INCREASE!
 
const C      = 0.010;   # This is the membrane (specific) capacitance [uF/mm^2]
const gnamax = 1.2;     # This is the membrane max (specific) sodium conductance [mS/mm^2]
const gkmax  = 0.36;    # This is the membrane max (specific) potassium conductance [mS/mm^2]
const gl     = 0.003;   # This is the membrane max (specific) leak conductance [mS/mm^2]

const Ena    = 50.;     # This is the reversal potential for sodium currents [mV]
const Ek     = -77.;    # This is the reversal potential for potassium currents [mV]
const El     = -54.387; # This is the reversal potential for leak currents [mV];

  Updating registry at `~/.julia/registries/General`
  Updating git-repo `https://github.com/JuliaRegistries/General.git`
Fetching: [========================================>]  100.0 %.0 % Resolving package versions...
  Updating `~/.julia/environments/v1.3/Project.toml`
 [no changes]
  Updating `~/.julia/environments/v1.3/Manifest.toml`
 [no changes]
 Resolving package versions...
  Updating `~/.julia/environments/v1.3/Project.toml`
 [no changes]
  Updating `~/.julia/environments/v1.3/Manifest.toml`
 [no changes]


┌ Info: Precompiling Plots [91a5bcdd-55d7-5caf-9e0b-520d859cae80]
└ @ Base loading.jl:1273


HTML{String}("<script>\n// Immediately-invoked-function-expression to avoid global variables.\n(function() {\n    var warning_div = document.getElementById(\"webio-warning-15732400558127761410\");\n    var hide = function () {\n        var script = document.getElementById(\"webio-setup-4923851510931662229\");\n        var parent = script && script.parentElement;\n        var grandparent = parent && parent.parentElement;\n        if (grandparent) {\n            grandparent.style.display = \"none\";\n        }\n        warning_div.style.display = \"none\";\n    };\n    if (typeof Jupyter !== \"undefined\") {\n        console.log(\"WebIO detected Jupyter notebook environment.\");\n        // Jupyter notebook.\n        var extensions = (\n            Jupyter\n            && Jupyter.notebook.config.data\n            && Jupyter.notebook.config.data.load_extensions\n        );\n        if (extensions && extensions[\"webio-jupyter-notebook\"]) {\n            // Extension already loaded.\n            console.log(\"Jupyter WebIO nbextension detected; not loading ad-hoc.\");\n            hide();\n            return;\n        }\n    } else if (window.location.pathname.includes(\"/lab\")) {\n        // Guessing JupyterLa\n        console.log(\"Jupyter Lab detected; make sure the @webio/jupyter-lab-provider labextension is installed.\");\n        hide();\n        return;\n    }\n})();\n\n</script>\n<p\n    id=\"webio-warning-15732400558127761410\"\n    class=\"output_text output_stderr\"\n    style=\"padding: 1em; font-weight: bold;\"\n>\n    Unable to load WebIO. Please make sure WebIO works for your Jupyter client.\n    For troubleshooting, please see <a href=\"https://juliagizmos.github.io/WebIO.jl/latest/providers/ijulia/\">\n    the WebIO/IJulia documentation</a>.\n    <!-- TODO: link to installation docs. -->\n</p>\n")

Now, let's initialise the model state variables and the simulation variables.

In [2]:
time = 0:Δt:T;        # This array of variables contains the "current time" [ms]
N    = length(time);  # This is the length of the array "time", i.e. how many discrete time steps;

In [3]:
function HH(I)
    W    = zeros(N,1)  # This is a "vector" or "array" where we want to "record" V as the time goes by
    Nspikes = 0        # Counter for the number of spikes 
    
  # Initial conditions:
    V      = El#-64.9964 
     αm = 0.1 * (V+40.) / (1. - exp(-(V+40.)/10.))
     βm  = 4. * exp(-0.0556 * (V+65))

     αn = 0.01 * (V+55) / (1. - exp(-(V+55.)/10.))
     βn = 0.125 * exp(-(V+65.)/80.)

     αh = 0.07 * exp(-0.05*(V+65.))
     βh = 1. / (1. + exp(-0.1*(V+35.)))
    
    m      = αm/(αm+βm)#0.0530 
    h      = αh/(αh+βh)#0.5960 
    n      = αn/(αn+βn)#0.3177 
    
    tmp    = 0        # For the peak detection    
        
    for k=1:N
     # Kinetic rates are expressed in msec
     αm = 0.1 * (V+40.) / (1. - exp(-(V+40.)/10.))
     βm  = 4. * exp(-0.0556 * (V+65))

     αn = 0.01 * (V+55) / (1. - exp(-(V+55.)/10.))
     βn = 0.125 * exp(-(V+65.)/80.)

     αh = 0.07 * exp(-0.05*(V+65.))
     βh = 1. / (1. + exp(-0.1*(V+35.)))

     n     = n + Δt * (αn * (1-n) - βn * n)        
     m     = m + Δt * (αm * (1-m) - βm * m)       
     h     = h + Δt * (αh * (1-h) - βh * h)       

     Ina   = gnamax * m^3 * h * (Ena - V)
     Ik    = gkmax  * n^4 * (Ek - V)
     Ileak = gl     * (El - V)
     V     = V + Δt/C * (Ina + Ik + Ileak + I)  
            
     W[k]  = V; 
            
     if (tmp==0) && (V>-10)     # Detection of a "peak", with positive derivative
        tmp = 1;                
        Nspikes = Nspikes + 1;
     elseif (tmp==1) && (V<-10) # if the "peak" occurs with negative derivative, ignore it
        tmp = 0;
     end #if
            
    end # for

    freq = round(1000. * Nspikes / T) 
    
return W, freq    
end

HH (generic function with 1 method)

In [4]:
using WebIO
WebIO.install_jupyter_nbextension()

gr(size=(1000,500), legend= false)

mp = @manipulate for I in slider(-0.18:0.01:0.5, label="I", value=-0.135)
    W, freq = HH(I)
    
    mystr = "AP frequency: $(freq) Hz";                                     # This is a string for the graph legend

    plot(time, W, color=:black, linewidth=3, leg=:false)#, box=false, border=false, ticks=false, left_margin = 3mm)         
    plot!(time,(-I/gl) * exp.(-time*gl/C) + (I/gl+El)*ones(N,1), color=:blue, linewidth=1, leg=:false)#, box=false, border=false, ticks=false, left_margin = 3mm) 
    
    xlabel!("time [ms]")                              # Label for the horizontal axis
    ylabel!("Membrane potential [mV]")                 # Label for the vertical axis

    xlims!(0, 150)
    ylims!(-100,30)
    
    annotate!(100,-80, mystr)
end


┌ Info: Installing Jupyter WebIO extension...
│   cmd = `/Users/giulia/.julia/conda/3/bin/jupyter nbextension install --user /Users/giulia/.julia/packages/WebIO/2nnB1/deps/bundles/webio-jupyter-notebook.js`
└ @ WebIO /Users/giulia/.julia/packages/WebIO/2nnB1/deps/jupyter.jl:237
Up to date: /Users/giulia/Library/Jupyter/nbextensions/webio-jupyter-notebook.js

    To initialize this nbextension in the browser every time the notebook (or other app) loads:
    
          jupyter nbextension enable <the entry point> --user
    
┌ Info: Enabling Jupyter WebIO extension...
│   cmd = `/Users/giulia/.julia/conda/3/bin/jupyter nbextension enable --user webio-jupyter-notebook`
└ @ WebIO /Users/giulia/.julia/packages/WebIO/2nnB1/deps/jupyter.jl:241
Enabling notebook extension webio-jupyter-notebook...
      - Validating: OK


Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Scope(Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{WebIO.DOM}(WebIO.DOM(:html, :label), Any["I"], Dict{Symbol,Any}(:className => "interact ",:style => Dict{Any,Any}(:padding => "5px 10px 0px 10px")))], Dict{Symbol,Any}(:className => "interact-flex-row-left")), Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{WebIO.DOM}(WebIO.DOM(:html, :input), Any[], Dict{Symbol,Any}(:max => 69,:min => 1,:attributes => Dict{Any,Any}(:type => "range",Symbol("data-bind") => "numericValue: index, valueUpdate: 'input', event: {change: function (){this.changes(this.changes()+1)}}","orient" => "horizontal"),:step => 1,:className => "slider slider is-fullwidth",:style => Dict{Any,Any}()))], Dict{Symbol,Any}(:className => "interact-flex-row-center")), Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{WebIO.DOM}(WebIO.DOM(:html, :p), Any[], Dict{Symbol,Any}(:attributes => Dict("data-bind" => "text: formatted_val")))], Dict{Symbol,Any}(:className => "interact-flex-row-right"))], Dict{Symbol,Any}(:className => "interact-flex-row interact-widget")), Dict{String,Tuple{Observables.AbstractObservable,Union{Nothing, Bool}}}("changes" => (Observable{Int64} with 1 listeners. Value:
0, nothing),"index" => (Observable{Any} with 2 listeners. Value:
6, nothing)), Set(String[]), nothing, Asset[Asset("js", "knockout", "/Users/giulia/.julia/packages/Knockout/1sDlc/src/../assets/knockout.js"), Asset("js", "knockout_punches", "/Users/giulia/.julia/packages/Knockout/1sDlc/src/../assets/knockout_punches.js"), Asset("js", nothing, "/Users/giulia/.julia/packages/InteractBase/9mFwe/src/../assets/all.js"), Asset("css", nothing, "/Users/giulia/.julia/packages/InteractBase/9mFwe/src/../assets/style.css"), Asset("css", nothing, "/Users/giulia/.julia/packages/Interact/SbgIk/src/../assets/bulma_confined.min.css")], Dict{Any,Any}("changes" => Any[WebIO.JSString("(function (val){return (val!=this.model[\"changes\"]()) ? (this.valueFromJulia[\"changes\"]=true, this.model[\"changes\"](val)) : undefined})")],"index" => Any[WebIO.JSString("(function (val){return (val!=this.model[\"index\"]()) ? (this.valueFromJulia[\"index\"]=true, this.model[\"index\"](val)) : undefined})")]), WebIO.ConnectionPool(Channel{Any}(sz_max:32,sz_curr:0), Set(AbstractConnection[]), Base.GenericCondition{Base.AlwaysLockedST}(Base.InvasiveLinkedList{Task}(Task (runnable) @0x000000011a032ad0, Task (runnable) @0x000000011a032ad0), Base.AlwaysLockedST(1))), WebIO.JSString[WebIO.JSString("function () {\n    var handler = (function (ko, koPunches) {\n    ko.punches.enableAll();\n    ko.bindingHandlers.numericValue = {\n        init: function(element, valueAccessor, allBindings, data, context) {\n            var stringified = ko.observable(ko.unwrap(valueAccessor()));\n            stringified.subscribe(function(value) {\n                var val = parseFloat(value);\n                if (!isNaN(val)) {\n                    valueAccessor()(val);\n                }\n            });\n            valueAccessor().subscribe(function(value) {\n                var str = JSON.stringify(value);\n                if ((str == \"0\") && ([\"-0\", \"-0.\"].indexOf(stringified()) >= 0))\n                     return;\n                 if ([\"null\", \"\"].indexOf(str) >= 0)\n                     return;\n                stringified(str);\n            });\n            ko.applyBindingsToNode(\n                element,\n                {\n                    value: stringified,\n                    valueUpdate: allBindings.get('valueUpdate'),\n                },\n                context,\n            );\n        }\n    };\n    var json_data = {\"formatted_vals\":[\"-0.18\",\"-0.17\",\"-0.16\",\"-0.15\",\"-0.14\",\"-0.13\",\"-0.12\",\"-0.11\",\"-0.1\",\"-0.09\",\"-0.08\",\"-0.07\",\"-0.06\",\"-0.05\",\"-0.04\",\"-0.03\",\"-0.02\",\"-0.01\",\"0.0\",\"0.01\",\"0.02\",\"0.03\",\"0.04\",\"0.05\",\"0.06\",\"0.0

In [5]:
function HH2(Iext)
    W    = zeros(N,1)  # This is a "vector" or "array" where we want to "record" V as the time goes by
    Nspikes = 0        # Counter for the number of spikes 
    
  # Initial conditions:
    V      = -64.9964 
    m      = 0.0530 
    h      = 0.5960 
    n      = 0.3177 
    
    tmp    = 0        # For the peak detection    
        
    for k=1:N
     # Kinetic rates are expressed in msec
     αm = 0.1 * (V+40.) / (1. - exp(-(V+40.)/10.))
     βm  = 4. * exp(-0.0556 * (V+65))

     αn = 0.01 * (V+55) / (1. - exp(-(V+55.)/10.))
     βn = 0.125 * exp(-(V+65.)/80.)

     αh = 0.07 * exp(-0.05*(V+65.))
     βh = 1. / (1. + exp(-0.1*(V+35.)))

     n     = n + Δt * (αn * (1-n) - βn * n)        
     m     = m + Δt * (αm * (1-m) - βm * m)       
     h     = h + Δt * (αh * (1-h) - βh * h)       

     Ina   = gnamax * m^3 * h * (Ena - V)
     Ik    = gkmax  * n^4 * (Ek - V)
     Ileak = gl     * (El - V)
     V     = V + Δt/C * (Ina + Ik + Ileak + Iext[k])  
            
     W[k]  = V; 
            
     if (tmp==0) && (V>-10)     # Detection of a "peak", with positive derivative
        tmp = 1;                
        Nspikes = Nspikes + 1;
     elseif (tmp==1) && (V<-10) # if the "peak" occurs with negative derivative, ignore it
        tmp = 0;
     end #if
            
    end # for
    
return W    
end

HH2 (generic function with 1 method)

In [8]:
gr(size=(1000,500), legend= false)

s1 = slider(0:0.05:20, label="Io", value=0)
s2 = slider(0:0.05:20, label="I1", value=0)
s3 = slider(Δt:Δt:50, label="T", value=30)

mp = @manipulate for Io in s1, I1 in s2, To in s3

    delay = 10.

    i1 = 0:Δt:delay
    i2 = (i1[end] + Δt):Δt:(i1[end] + Δt + 2*Δt)
    i3 = (i2[end] + Δt):Δt:(i2[end] + Δt + To)
    i4 = (i3[end] + Δt):Δt:(i3[end] + Δt + 2*Δt)
    i5 = (i4[end] + Δt):Δt:T

    M1 = length(i1)
    M2 = length(i2)
    M3 = length(i3)
    M4 = length(i4)
    M5 = length(i5)

    Iext = [zeros(M1,1); Io .* ones(M2,1); zeros(M3,1); I1 .* ones(M4,1); zeros(M5,1)]
    
    W = HH2(Iext)

    plot(time, W, color=:black, linewidth=3, leg=:false)#, box=false, border=false, ticks=false, left_margin = 3mm)         
    plot!(time, Iext, color=:red, linewidth=3, leg=:false)#, box=false, border=false, ticks=false, left_margin = 3mm)         

    xlabel!("time [ms]")                              # Label for the horizontal axis
    ylabel!("Membrane potential [mV]")                 # Label for the vertical axis

    xlims!(0, 50)
    ylims!(-100,50)
    
    annotate!(40,-80, "V(t)")

    annotate!(40,10, text("I(t)", 16, :red, :center))
end


Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Scope(Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{WebIO.DOM}(WebIO.DOM(:html, :label), Any["Io"], Dict{Symbol,Any}(:className => "interact ",:style => Dict{Any,Any}(:padding => "5px 10px 0px 10px")))], Dict{Symbol,Any}(:className => "interact-flex-row-left")), Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{WebIO.DOM}(WebIO.DOM(:html, :input), Any[], Dict{Symbol,Any}(:max => 401,:min => 1,:attributes => Dict{Any,Any}(:type => "range",Symbol("data-bind") => "numericValue: index, valueUpdate: 'input', event: {change: function (){this.changes(this.changes()+1)}}","orient" => "horizontal"),:step => 1,:className => "slider slider is-fullwidth",:style => Dict{Any,Any}()))], Dict{Symbol,Any}(:className => "interact-flex-row-center")), Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{WebIO.DOM}(WebIO.DOM(:html, :p), Any[], Dict{Symbol,Any}(:attributes => Dict("data-bind" => "text: formatted_val")))], Dict{Symbol,Any}(:className => "interact-flex-row-right"))], Dict{Symbol,Any}(:className => "interact-flex-row interact-widget")), Dict{String,Tuple{Observables.AbstractObservable,Union{Nothing, Bool}}}("changes" => (Observable{Int64} with 1 listeners. Value:
0, nothing),"index" => (Observable{Any} with 2 listeners. Value:
1, nothing)), Set(String[]), nothing, Asset[Asset("js", "knockout", "/Users/giulia/.julia/packages/Knockout/1sDlc/src/../assets/knockout.js"), Asset("js", "knockout_punches", "/Users/giulia/.julia/packages/Knockout/1sDlc/src/../assets/knockout_punches.js"), Asset("js", nothing, "/Users/giulia/.julia/packages/InteractBase/9mFwe/src/../assets/all.js"), Asset("css", nothing, "/Users/giulia/.julia/packages/InteractBase/9mFwe/src/../assets/style.css"), Asset("css", nothing, "/Users/giulia/.julia/packages/Interact/SbgIk/src/../assets/bulma_confined.min.css")], Dict{Any,Any}("changes" => Any[WebIO.JSString("(function (val){return (val!=this.model[\"changes\"]()) ? (this.valueFromJulia[\"changes\"]=true, this.model[\"changes\"](val)) : undefined})")],"index" => Any[WebIO.JSString("(function (val){return (val!=this.model[\"index\"]()) ? (this.valueFromJulia[\"index\"]=true, this.model[\"index\"](val)) : undefined})")]), WebIO.ConnectionPool(Channel{Any}(sz_max:32,sz_curr:0), Set(AbstractConnection[]), Base.GenericCondition{Base.AlwaysLockedST}(Base.InvasiveLinkedList{Task}(Task (runnable) @0x00000001164ad450, Task (runnable) @0x00000001164ad450), Base.AlwaysLockedST(1))), WebIO.JSString[WebIO.JSString("function () {\n    var handler = (function (ko, koPunches) {\n    ko.punches.enableAll();\n    ko.bindingHandlers.numericValue = {\n        init: function(element, valueAccessor, allBindings, data, context) {\n            var stringified = ko.observable(ko.unwrap(valueAccessor()));\n            stringified.subscribe(function(value) {\n                var val = parseFloat(value);\n                if (!isNaN(val)) {\n                    valueAccessor()(val);\n                }\n            });\n            valueAccessor().subscribe(function(value) {\n                var str = JSON.stringify(value);\n                if ((str == \"0\") && ([\"-0\", \"-0.\"].indexOf(stringified()) >= 0))\n                     return;\n                 if ([\"null\", \"\"].indexOf(str) >= 0)\n                     return;\n                stringified(str);\n            });\n            ko.applyBindingsToNode(\n                element,\n                {\n                    value: stringified,\n                    valueUpdate: allBindings.get('valueUpdate'),\n                },\n                context,\n            );\n        }\n    };\n    var json_data = {\"formatted_vals\":[\"0.0\",\"0.05\",\"0.1\",\"0.15\",\"0.2\",\"0.25\",\"0.3\",\"0.35\",\"0.4\",\"0.45\",\"0.5\",\"0.55\",\"0.6\",\"0.65\",\"0.7\",\"0.75\",\"0.8\",\"0.85\",\"0.9\",\"0.95\",\"1.0\",\"1.05\",\"1.1\",\"1.15\",\"1.2\",\"1.25\",\"1.3\",\"1.35\",\"1.4\

In [9]:
rand()

0.8584907396213801

In [11]:
rand()<0.2

false